In [5]:
!pip install annoy

     |████████████████████████████████| 655kB 8.4MB/s 
  Created wheel for annoy: filename=annoy-1.17.0-cp37-cp37m-linux_x86_64.whl size=391611 sha256=305f68c5aea70770bf7780e10419ec19637264c39ae4ba17f0fdbd8349bb2a77
  Stored in directory: /root/.cache/pip/wheels/3a/c5/59/cce7e67b52c8e987389e53f917b6bb2a9d904a03246fadcb1e
Successfully built annoy


In [6]:
from scipy import spatial
import matplotlib.pyplot as plt
import tensorflow as tf
import tensorflow_hub as hub
# For saving 'feature vectors' into a txt file
import numpy as np
# Glob for reading file names in a folder
import glob
import os.path
from tqdm import tqdm
import ntpath
import warnings
import cv2
from annoy import AnnoyIndex
from scipy import spatial
warnings.filterwarnings('ignore')
from operator import itemgetter
from google.colab import drive


In [7]:
# Uncomment the code to mount the drive 
drive.mount('/content/drive')


Mounted at /content/drive


In [8]:
# Uncomment to code to unzip images 
!unzip '/content/drive/MyDrive/ADM/Assi3Data/sampleimages.zip' -d '/content/'

Streaming output truncated to the last 5000 lines.
  inflating: /content/sampleimages/1000010562_168146_1.jpeg  
  inflating: /content/sampleimages/1000010562_168146_2.jpeg  
  inflating: /content/sampleimages/1000010562_168146_3.jpeg  
  inflating: /content/sampleimages/1000010562_168146_4.jpeg  
  inflating: /content/sampleimages/1000010562_204480_1.jpeg  
  inflating: /content/sampleimages/1000010562_204480_2.jpeg  
  inflating: /content/sampleimages/1000010562_204480_3.jpeg  
  inflating: /content/sampleimages/1000010562_204480_4.jpeg  
  inflating: /content/sampleimages/1000010562_212334_1.jpeg  
  inflating: /content/sampleimages/1000010562_212334_2.jpeg  
  inflating: /content/sampleimages/1000010562_214433_1.jpeg  
  inflating: /content/sampleimages/1000010562_214433_2.jpeg  
  inflating: /content/sampleimages/1000010562_214433_3.jpeg  
  inflating: /content/sampleimages/1000010562_214433_4.jpeg  
  inflating: /content/sampleimages/1000010562_219007_1.jpeg  
  inflating: /conte

In [18]:
def load_img(path):
    # Reads the image file and returns data type of string
    img = tf.io.read_file(path)
    # Decodes the image to W x H x 3 shape tensor with type of uint8
    img = tf.io.decode_jpeg(img, channels=3)
    # Resizes the image to 224 x 224 x 3 shape tensor
    img = tf.image.resize_with_pad(img, 224, 224)
    # Converts the data type of uint8 to float32 by adding a new axis
    # img becomes 1 x 224 x 224 x 3 tensor with data type of float32
    # This is required for the mobilenet model we are using
    img = tf.image.convert_image_dtype(img,tf.float32)[tf.newaxis, ...]

    return img

In [11]:
def match_id(filename):
    product_id = '_'.join(filename.split('_')[:-1])
    return product_id

In [ ]:
image_paths = glob.glob('/content/drive/MyDrive/ADM/Assi3Data/sampleimages/*.jpeg')
print(f'Founnd [{len(image_paths)}] images')


Founnd [9191] images


In [17]:
def get_image_feature_vectors(path):
    module_handle = "https://tfhub.dev/google/imagenet/mobilenet_v2_140_224/feature_vector/4"
    # Loads the module
    module = hub.load(module_handle)
    # Loops through all images in a local folder

    #print(path)
    # Loads and pre-process the image
    img = load_img(path)
    # Calculate the image feature vector of the img
    features = module(img)
    # Remove single-dimensional entries from the 'features' array  
    feature_set = np.squeeze(features)

    # Saves the image feature vectors into a file for later use
    outfile_name = os.path.basename(filename) + ".npz"

    out_path = os.path.join('/content/drive/MyDrive/ADM/Assi3Data/sampleimages/',outfile_name)
    # Saves the 'feature_set' to a text file
    np.savetxt(out_path, feature_set, delimiter=',')

In [16]:
def get_features(img, image_path): 
     # Definition of module with using tfhub.dev
    module_handle = "https://tfhub.dev/google/imagenet/mobilenet_v2_140_224/feature_vector/4"
    # Loads the module
    module = hub.load(module_handle)
    features = module(img)
    # Remove single-dimensional entries from the 'features' array  
    feature_set = np.squeeze(features)
    #print(image_path)

    # Saves the image feature vectors into a file for later use
    outfile_name = os.path.basename(image_path) + ".npz"

    out_path = os.path.join('/content/drive/MyDrive/ADM/Assi3Data/sampleimages/',outfile_name)
    # Saves the 'feature_set' to a text file
    np.savetxt(out_path, feature_set, delimiter=',')
    vector = np.loadtxt(out_path)
    return vector
    

In [ ]:
image_paths= glob.glob(r'/content/drive/MyDrive/ADM/Assi3Data/sampleimages/*.jpeg')
print(image_paths)

['/content/images/sampleimages/1000016965_1608434_4.jpeg', '/content/images/sampleimages/1000005597_2499654_1.jpeg', '/content/images/sampleimages/1000004228_1061759_1.jpeg', '/content/images/sampleimages/1000018606_2084594_2.jpeg', '/content/images/sampleimages/1000004298_181826_3.jpeg', '/content/images/sampleimages/1000002181_2206540_1.jpeg', '/content/images/sampleimages/1000010410_91658_2.jpeg', '/content/images/sampleimages/1000015900_3730326_1.jpeg', '/content/images/sampleimages/1000006044_2941495_3.jpeg', '/content/images/sampleimages/1000014204_188870_1.jpeg', '/content/images/sampleimages/1000017643_1678329_1.jpeg', '/content/images/sampleimages/1000018483_401287_4.jpeg', '/content/images/sampleimages/1000002999_4372504_3.jpeg', '/content/images/sampleimages/1000016486_272916_3.jpeg', '/content/images/sampleimages/1000018433_320953_3.jpeg', '/content/images/sampleimages/1000019184_907941_4.jpeg', '/content/images/sampleimages/1000018977_1150402_2.jpeg', '/content/images/samp

In [ ]:
image_paths= glob.glob('/content/drive/MyDrive/ADM/Assi3Data/sampleimages/*.jpeg')
vectorfiles = glob.glob('/content/drive/MyDrive/ADM/Assi3Data/sampleimages/*.npz')
# compute styles
image_style_embeddings = {}
i = 0 
chunk_size = 2500
while i < 10000:
  for image_path in tqdm(image_paths[i:chunk_size]): 
      image_tensor = load_img(image_path)
      vector = get_features(image_tensor, image_path)
      image_style_embeddings[ntpath.basename(image_path)] = vector

      i+=chunk_size
      chunk_size += chunk_size
    

  0%|          | 4/2500 [00:38<8:38:48, 12.47s/it] 

  0%|          | 5/2500 [00:40<6:30:34,  9.39s/it]

  0%|          | 6/2500 [00:42<4:59:31,  7.21s/it]

  0%|          | 7/2500 [00:44<3:53:00,  5.61s/it]

  0%|          | 8/2500 [00:46<3:09:33,  4.56s/it]

...

100%|█████████▉| 2496/2500 [1:28:38<00:08,  2.21s/it]

100%|█████████▉| 2497/2500 [1:28:40<00:06,  2.20s/it]

100%|█████████▉| 2498/2500 [1:28:42<00:04,  2.14s/it]

100%|█████████▉| 2499/2500 [1:28:45<00:02,  2.17s/it]

100%|██████████| 2500/2500 [1:28:47<00:00,  2.13s/it]


In [ ]:
image_style_embeddings

{'1000000461_1024049_1.jpeg': array([1.28601062, 0.88914758, 0.        , ..., 0.        , 0.06295194,
        0.10286042]),
 '1000000461_1024049_2.jpeg': array([0.10065432, 1.76269507, 0.        , ..., 0.        , 0.11119665,
        0.03740077]),
 '1000000461_1024049_3.jpeg': array([0.01989896, 0.        , 0.        , ..., 0.        , 0.        ,
        0.04100302]),
 '1000000461_1024049_4.jpeg': array([0.63666391, 0.42368767, 0.01233391, ..., 0.        , 0.04679585,
        0.        ]),
 '1000000461_1048200_1.jpeg': array([1.52672243, 1.17874789, 0.        , ..., 0.06280511, 0.        ,
        0.4563005 ]),
 '1000000461_1048200_2.jpeg': array([0.3217988 , 0.17242597, 0.        , ..., 0.07596476, 0.        ,
        0.83456022]),
 '1000000461_1048200_3.jpeg': array([0.49379   , 0.15931246, 0.        , ..., 0.05556992, 0.        ,
        0.78813583]),
 '1000000461_105915_1.jpeg': array([0.08548968, 0.66111737, 0.07026011, ..., 0.09598131, 1.16288722,
        0.01163385]),
 '1000000

In [ ]:
# Unzipping images 
!unzip '/content/drive/MyDrive/ADM/Assi3Data/npz.zip' -d '/content/'

In [15]:
def cluster():
    print("-------Annoy Index Generation----------------")
    # Defining data structures as empty dict
    file_index_to_file_name = {}
    file_index_to_file_vector = {}
    file_index_to_product_id = {}
    # Configuring annoy parameters
    dims = 1792
    n_nearest_neighbors = 20
    trees = 10000
    # Reads all file names which stores feature vectors
    allfiles = glob.glob('/content/npz/*.npz')

    t = AnnoyIndex(dims, metric='angular')
    
    for file_index, i in enumerate(allfiles):
    # Reads feature vectors and assigns them into the file_vector 
        file_vector = np.loadtxt(i)

        # Assigns file_name, feature_vectors and corresponding product_id
        file_name = os.path.basename(i).split('.')[0]
        file_index_to_file_name[file_index] = file_name
        file_index_to_file_vector[file_index] = file_vector
        file_index_to_product_id[file_index] = match_id(file_name)

        # Adds image feature vectors into annoy index   
        t.add_item(file_index, file_vector)

        print("---------------------------------")
        print("Annoy index     : %s" %file_index)
        print("Image file name : %s" %file_name)
        print("Product id      : %s" %file_index_to_product_id[file_index])
        #print("--- %.2f minutes passed ---------" % ((time.time() - start_time)/60))


    # Builds annoy index
    t.build(trees)

    print ("Step.1 - ANNOY index generation - Finished")
    print ("Step.2 - Similarity score calculation - Started ") 
  
    global named_nearest_neighbors
    named_nearest_neighbors = []

  # Loops through all indexed items
    for i in file_index_to_file_name.keys():

    # Assigns master file_name, image feature vectors and product id values
        master_file_name = file_index_to_file_name[i]
        master_vector = file_index_to_file_vector[i]
        master_product_id = file_index_to_product_id[i]

        # Calculates the nearest neighbors of the master item
        nearest_neighbors = t.get_nns_by_item(i, n_nearest_neighbors)

        # Loops through the nearest neighbors of the master item
        for j in nearest_neighbors:

            # Assigns file_name, image feature vectors and product id values of the similar item
            neighbor_file_name = file_index_to_file_name[j]
            neighbor_file_vector = file_index_to_file_vector[j]
            neighbor_product_id = file_index_to_product_id[j]

            # Calculates the similarity score of the similar item
            similarity = 1 - spatial.distance.cosine(master_vector, neighbor_file_vector)
            rounded_similarity = int((similarity * 10000)) / 10000.0

            # Appends master product id with the similarity score 
            # and the product id of the similar items
            named_nearest_neighbors.append({
            'similarity': rounded_similarity,
            'master_pi': master_product_id,
            'similar_pi': neighbor_product_id})
  
    with open('nearest_neighbors.json', 'w') as out:
      json.dump(named_nearest_neighbors, out)



In [12]:
image_paths = glob.glob('/content/sampleimages/*.jpeg')
print(f'Founnd [{len(image_paths)}] images')

images = []
for image_path in image_paths:
    image = cv2.imread(image_path, 3)
    b,g,r = cv2.split(image)           # get b, g, r
    image = cv2.merge([r,g,b])         # switch it to r, g, b
    image = cv2.resize(image, (200, 200))
    product_id = match_id(ntpath.basename(image_path))
    images.append({
      'image_path' : ntpath.basename(image_path),
        'image' : image,
       'product_id':product_id
    })


Founnd [9191] images


In [13]:
def search_similar_image(reference_image, max_results):
    reference_image = '_'.join(reference_image.split('_')[:-1])
    print(reference_image)
    nearest = []
    for i in range (0, len(named_nearest_neighbors)):
        if(named_nearest_neighbors[i]['master_pi'] == reference_image):
            nearest.append({
                'similarity' : named_nearest_neighbors[i]['similarity'],
                'master_pi' : named_nearest_neighbors[i]['master_pi'],
                'similar_pi' : named_nearest_neighbors[i]['similar_pi']
            })
    f, ax = plt.subplots(1, max_results, figsize=(16, 8))
    for i in range(0, max_results):
        for j in range(0, len(images)):
            if(nearest[i]['similar_pi'] == images[j]['product_id']):
                ax[i].imshow(images[j]['image'])
                ax[i].set_axis_off()
                
    plt.show()

                
        